In [40]:
import numpy as np
import pandas as pd
from scipy.stats import chi2_contingency

pd.set_option("display.max_rows", 50000)

In [41]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [42]:
merged_data = pd.read_csv("/content/drive/MyDrive/Fiverr/PROJECT_MIMI/Fund_Settlement_Security_Stocks_Ratings.csv", parse_dates=["data_date"])

/usr/local/lib/python3.7/dist-packages/IPython/core/interactiveshell.py:2718: DtypeWarning: Columns (9,15,25,29,919,920,926,935,936,941,943,945,956,959,965,978,984,989,992,993,996,997,1009,1014,1015,1016,1017,1018,1019,1020,1021,1024,1025,1028,1029,1031,1033,1034,1035,1036,1041,1042,1053,1055,1056,1057,1058,1059,1066,1071,1072,1074,1075,1076,1077,1084,1091,1098,1101,1102,1103,1105,1106,1116,1119,1120,1121,1122,1124,1125,1735,1736,1737,1738,1756,1757,1762,1766) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [43]:
merged_data.shape

(17123, 1782)

In [44]:
merged_data.rename(
    columns={"iqv-s&p_domestic_long_term_issuer_credit_rating": "s&p_domestic_long_term_issuer_credit_rating", 
             "iqv-s&p_domestic_short_term_issuer_credit_rating": "s&p_domestic_short_term_issuer_credit_rating"}, inplace=True)

In [45]:
merged_data.columns

Index(['global_company_key', 'data_date', 'data_year_-_fiscal',
       'industry_format', 'level_of_consolidation_-_company_annual_descriptor',
       'population_source', 'data_format', 'ticker_symbol', 'company_name',
       'adoption_of_accounting_changes',
       ...
       'dividends_per_share_-_ex_date_-_monthly',
       'dividends_per_share_-_pay_date_-_monthly',
       'common_stock_float_shares_-_canada', 'price_-_close_-_daily',
       'price_-_high_-_daily', 'price_-_low_-_daily', 'price_-_open_-_daily',
       'price_status_code_-_daily',
       's&p_domestic_long_term_issuer_credit_rating',
       's&p_domestic_short_term_issuer_credit_rating'],
      dtype='object', length=1782)

In [46]:
merged_data["year"] = merged_data["data_date"].apply(lambda x: x.strftime("%Y"))

In [47]:
constant_columns = sorted(['price_-_close_-_daily', 'price_-_high_-_daily', 'price_-_low_-_daily', 'price_-_open_-_daily', 
                    'price_status_code_-_daily', "dividend_rate_-_monthly", 'dividends_per_share_-_ex_date_-_monthly', 
                    'dividends_per_share_-_pay_date_-_monthly', 'common_stock_float_shares_-_canada', 'iso_currency_code_-_monthly', 
                    "settlementamount", "sued", "global_company_key", "ticker_symbol", "s&p_domestic_short_term_issuer_credit_rating", 
                    "s&p_domestic_long_term_issuer_credit_rating", "year"])

In [48]:
data_ = merged_data[constant_columns]
data_.drop_duplicates(subset=["global_company_key"], keep="first", inplace=True)

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


In [49]:
missing_columns = merged_data[sorted(list(set(merged_data.columns) - set(sorted(constant_columns))))].isnull().sum().reset_index().rename(columns={0: "total_missing", "index": "md_columns"})
missing_columns["percentage_missing"] = missing_columns["total_missing"].apply(lambda x: (x/merged_data.shape[0]) * 100)
missing_columns = missing_columns[missing_columns["percentage_missing"] > 50]

In [50]:
numerical_variables = list()
categorical_variables = list()

for column in merged_data[missing_columns[missing_columns["percentage_missing"] > 50]["md_columns"].unique()]:
  if merged_data[column].dtype in ["float64", "int64"]:
    numerical_variables.append(column)
    merged_data[column] = merged_data[column].apply(lambda x: round(x, 2))

  if merged_data[column].dtype == "object":
    categorical_variables.append(column)

In [51]:
merged_data.shape

(17123, 1783)

In [52]:
merged_data = merged_data.groupby(["global_company_key", "year"])[numerical_variables].agg("sum").reset_index()

In [53]:
merged_data.shape

(8724, 1490)

In [54]:
merged_data = merged_data.groupby(["global_company_key"])[numerical_variables].agg("mean").reset_index()

In [55]:
merged_data = pd.merge(merged_data, data_, on="global_company_key")
merged_data.drop(columns="year", inplace=True)

In [56]:
merged_data.shape

(2462, 1504)

In [57]:
merged_data.to_csv("/content/drive/MyDrive/Fiverr/PROJECT_MIMI/Final_DataSet.csv", index=False)

In [58]:
merged_data["sued"].value_counts()

no     2037
yes     425
Name: sued, dtype: int64

In [59]:
merged_data.dropna(subset=["s&p_domestic_long_term_issuer_credit_rating", "s&p_domestic_short_term_issuer_credit_rating"], inplace=True)

In [60]:
categorical_variables = list()
categorical_variables_ = list()

for column in merged_data.columns:
  if merged_data[column].dtype == "object":
    categorical_variables.append(column)
    merged_data[column] = merged_data[column].astype("category")
    merged_data[column+"_"] = merged_data[column].cat.codes
    categorical_variables_.append(column+"_")

  elif merged_data[column].dtype in ["float64", "int64"]:
    merged_data[column] = merged_data[column].apply(lambda x: round(x, 5))


In [61]:
merged_data[categorical_variables].head()

iso_currency_code_-_monthly sued ticker_symbol
0                         USD   no           AAN
1                         USD   no           ABT
2                         USD  yes           AET
3                         USD   no          ATRI
4                         USD  yes           ACV

In [62]:
for variable in categorical_variables:
  if variable != "sued":
    stat, p, dof, expected = chi2_contingency(pd.crosstab(merged_data[variable], merged_data["sued"]))
    
    if p <= 0.05:
      print(column)
      print("Reject null hypothesis")

    else:
      print("Fail to reject null hypothesis")

Fail to reject null hypothesis
Fail to reject null hypothesis


In [63]:
from sklearn.tree import DecisionTreeRegressor

X = merged_data[[column for column in merged_data.columns if column not in ["sued", "iso_currency_code_-_monthly", "ticker_symbol", "sued_", "settlementamount"]]]
y = merged_data["sued_"]

In [64]:
tree = DecisionTreeRegressor().fit(X, y)

In [68]:
indexed_column = list()

for i in range(0, len(list(tree.feature_importances_))):
  if list(tree.feature_importances_)[i] in sorted(list(tree.feature_importances_), reverse=True):
    if i != 0:
      indexed_column.append(i)

In [69]:
sorted(list(tree.feature_importances_), reverse=True)[1000]

0.0

In [70]:
for i in range(0, len(merged_data.columns)):
  if i in indexed_column:
    print(merged_data.columns[i])

acceptances_outstanding
acceptances_outstanding_data_code
accounting_changes_-_cumulative_effect
accounting_changes_-_cumulative_effect_data_code
accounting_changes_-_cumulative_effect_footnote
accounts_payable/creditors_-_brokers,_dealers,_and_clearing_organizations
accounts_payable/creditors_-_customer
accounts_payable/creditors_-_other_-_fs
accounts_payable/creditors_-_other_-_fs_data_code
accounts_payable_-_trade_data_code
accounts_payable_-_utility
accounts_payable_-_utility_data_code
accounts_payable_-_utility_footnote
accounts_payable_and_accrued_liabilities_-_increase/(decrease)
accounts_payable_and_accrued_liabilities_-_increase/(decrease)_data_code
accounts_receivable/debtors_-_brokers,_dealers,_and_clearing_organizations
accounts_receivable/debtors_-_customer
accounts_receivable/debtors_-_customer_data_code
accounts_receivable/debtors_-_customer_footnote
accounts_receivable/debtors_-_total
accounts_receivable/debtors_-_total_data_code
accounts_receivable/debtors_-_total_foot

In [71]:
merged_data.corr()

global_company_key  ...  ticker_symbol_
global_company_key                                            1.000000  ...       -0.023433
acceptances_outstanding                                            NaN  ...             NaN
acceptances_outstanding_data_code                                  NaN  ...             NaN
accounting_changes_-_cumulative_effect                        0.026998  ...       -0.030088
accounting_changes_-_cumulative_effect_data_code                   NaN  ...             NaN
accounting_changes_-_cumulative_effect_footnote                    NaN  ...             NaN
accounts_payable/creditors_-_brokers,_dealers,_...                 NaN  ...             NaN
accounts_payable/creditors_-_customer                              NaN  ...             NaN
accounts_payable/creditors_-_other_-_fs                            NaN  ...             NaN
accounts_payable/creditors_-_other_-_fs_data_code                  NaN  ...             NaN
accounts_payable_-_trade_data_code                                 NaN  ...             NaN
accounts_payable_-_utility                                         NaN  ...             NaN
accounts_payable_-_utility_data_code                               NaN  ...             NaN
accounts_payable_-_utility_footnote                                NaN  ...             NaN
accounts_payable_and_accrued_liabilities_-_incr...           -0.081996  ...        0.010449
accounts_payable_and_accrued_liabilities_-_incr...            0.004261  ...        0.017827
accounts_receivable/debtors_-_brokers,_dealers,...                 NaN  ...             NaN
accounts_receivable/debtors_-_customer                             NaN  ...             NaN
accounts_receivable/debtors_-_customer_data_code                   NaN  ...             NaN
accounts_receivable/debtors_-_customer_footnote                    NaN  ...             NaN
accounts_receivable/debtors_-_total                                NaN  ...             NaN
accounts_receivable/debtors_-_total_data_code                      NaN  ...             NaN
accounts_receivable/debtors_-_total_footnote                       NaN  ...             NaN
accounts_receivable_-_decrease_(increase)                     0.039985  ...       -0.025395
accounts_receivable_-_decrease_(increase)_data_...            0.012590  ...        0.032009
accounts_receivable_-_trade_-_utility                              NaN  ...             NaN
accounts_receivable_-_trade_-_utility_data_code                    NaN  ...             NaN
accrued_expenses                                             -0.120690  ...        0.022296
accrued_expenses_and_deferred_income                               NaN  ...             NaN
accrued_expenses_and_deferred_income_data_code                     NaN  ...             NaN
accrued_expenses_data_code                                    0.021888  ...       -0.024069
accrued_unbilled_revenues_(balance_sheet)                          NaN  ...             NaN
accrued_unbilled_revenues_(balance_sheet)_data_...                 NaN  ...             NaN
accum_other_comp_inc_-_derivatives_unrealized_g...            0.039215  ...       -0.013058
accum_other_comp_inc_-_derivatives_unrealized_g...           -0.039892  ...        0.002988
accum_other_comp_inc_-_min_pension_liab_adj                   0.100442  ...       -0.001698
accum_other_comp_inc_-_min_pension_liab_adj_dat...           -0.009581  ...        0.046644
accum_other_comp_inc_-_min_pension_liab_adj_foo...                 NaN  ...             NaN
accum_other_comp_inc_-_other_adjustments                      0.008141  ...       -0.011045
accum_other_comp_inc_-_unreal_g/l_ret_int_in_se...                 NaN  ...             NaN
accum_other_comp_inc_-_unreal_g/l_ret_int_in_se...                 NaN  ...             NaN
accumulated_depreciation_of_re_property                      -0.020371  ...       -0.023696
accumulated_other_comprehensive_income_(loss)                 0.099015  ...        0.008224
accu

In [ ]:
merged_data.isnull().sum()

global_company_key                                                                        0
acceptances_outstanding                                                                   0
acceptances_outstanding_data_code                                                         0
accounting_changes_-_cumulative_effect                                                    0
accounting_changes_-_cumulative_effect_data_code                                          0
accounting_changes_-_cumulative_effect_footnote                                           0
accounts_payable/creditors_-_brokers,_dealers,_and_clearing_organizations                 0
accounts_payable/creditors_-_customer                                                     0
accounts_payable/creditors_-_other_-_fs                                                   0
accounts_payable/creditors_-_other_-_fs_data_code                                         0
accounts_payable_-_trade_data_code                                              